In [1]:
# import AWS credentials
# import config.py ##for local
%run "/dbfs/FileStore/tables/config" ##for databricks

In [2]:
import pandas as pd
import numpy as np

from pyspark.sql import SparkSession
from pyspark import SparkFiles
from pyspark.sql import DataFrame
from pyspark.sql.types import *
import pyspark.sql.functions as F

In [3]:
# get or create Spark session
app_name = "spark-airbnb-sentiment"
spark = SparkSession.builder.appName(app_name).getOrCreate()

In [4]:
import boto3

secret_name = my_secret_name
region_name = my_region_name
access_key  = my_access_key
secret_key  = my_secret_key

session      = boto3.session.Session(aws_access_key_id=access_key, aws_secret_access_key=secret_key, region_name=region_name)
client       = session.client('secretsmanager')
secret_value = client.get_secret_value(SecretId=secret_name)

In [5]:
import json
def get_connection(secret_value):
    return json.loads(secret_value['SecretString'])

In [6]:
connection = get_connection(secret_value)

# Postgres credentials
jdbcHostname = connection['host']
jdbcPort     = connection['port']
jdbcDatabase = "postgres"
dialect      = "postgresql"
jdbcUsername = connection['username']
jdbcPassword = connection['password']

jdbcUrl = f"jdbc:{dialect}://{jdbcHostname}:{jdbcPort}/{jdbcDatabase}"
connectionProperties = {
  "user"     : jdbcUsername,
  "password" : jdbcPassword,
  "driver"   : "org.postgresql.Driver" 
}

In [7]:
# Read from reviews_full table

table = "reviews_full"

reviews_df = spark.read.jdbc(url=jdbcUrl, table=table, properties=connectionProperties)
reviews_df.printSchema()

root
-- listing_id: integer (nullable = true)
-- id: integer (nullable = true)
-- date: date (nullable = true)
-- reviewer_id: integer (nullable = true)
-- reviewer_name: string (nullable = true)
-- comments: string (nullable = true)

In [8]:
from pyspark.ml import Pipeline
import sparknlp
sparknlp.start()
from sparknlp.base import *
from sparknlp.annotator import *
from sparknlp.pretrained import PretrainedPipeline

pipeline = PretrainedPipeline("explain_document_ml", lang="en")

explain_document_ml download started this may take some time.
Approx size to download 9.4 MB
[ | ][ / ][ — ][ \ ][ | ][ / ][ — ][ \ ][ | ][ / ][ — ][OK!]

In [9]:
reviews_df = reviews_df.withColumnRenamed("comments", "text").filter("text IS NOT NULL").limit(100)

In [10]:
annotations_df = pipeline.transform(reviews_df)

In [11]:
display(annotations_df)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 34, 41, location, Map(sentence -> 0), List()), List(token, 43, 44, is, Map(sentence -> 0), List()), List(token, 46, 52, central, Map(sentence -> 0), List()), List(token, 54, 55, to, Map(sentence -> 0), List()), List(token, 57, 60, lots, Map(sentence -> 0), List()), List(token, 62, 63, of, Map(sentence -> 0), List()), List(token, 65, 72, shopping, Map(sentence -> 0), List()), List(token, 73, 73, ,, Map(sentence -> 0), List()), List(token, 75, 83, nightlife, Map(sentence -> 0), List()), List(token, 85, 87, and, Map(sentenc

In [12]:
ngrams = NGramGenerator() \
            .setInputCols(["token"]) \
            .setOutputCol("ngrams") \
            .setN(2) \
            .setEnableCumulative(False)

In [13]:
ngram_pipeline = Pipeline(
    stages = [
      ngrams
  ])

In [14]:
model = ngram_pipeline.fit(annotations_df)
extracted = model.transform(annotations_df)

In [15]:
display(extracted)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos ngrams 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) List(List(chunk, 0, 17, Very accommodating, Map(sentence -> 0), List()), List(chunk, 5, 18, accommodating ,, Map(sentence -> 0), List()), List(chunk, 18, 24, , great, Map(sentence -> 0), List()), List(chunk, 20, 30, great space, Map(sentence -> 0), List()), List(chunk, 26, 31, space ., Map(sentence -> 0), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 34, 41, location, Map(sentence -> 0), List()), List(token, 43, 44, is, Map(sentence -> 0), List()), List(token, 46, 52, central, Map(sentence -> 0), List()), List(token, 54, 55, to, Map(sentence -> 0), L

In [16]:
stop_words_cleaner = StopWordsCleaner() \
        .setInputCols(["token"]) \
        .setOutputCol("cleanTokens") \
        .setCaseSensitive(False) \
        .setStopWords(["this", "is", "and", ",", "!", ".", "\n", "\t", "ourselves", "hers", "between", "yourself", "but", "again", "there", "about", "once", "during", "out", "very", "having", "with", "they", "own", "an", "be", "some", "for", "do", "its", "yours", "such", "into", "of", "most", "itself", "other", "off", "is", "s", "am", "or", "who", "as", "from", "him", "each", "the", "themselves", "until", "below", "are", "we", "these", "your", "his", "through", "don", "nor", "me", "were", "her", "more", "himself", "this", "down", "should", "our", "their", "while", "above", "both", "up", "to", "ours", "had", "she", "all", "no", "when", "at", "any", "before", "them", "same", "and", "been", "have", "in", "will", "on", "does", "yourselves", "then", "that", "because", "what", "over", "why", "so", "can", "did", "not", "now", "under", "he", "you", "herself", "has", "just", "where", "too", "only", "myself", "which", "those", "i", "after", "few", "whom", "t", "being", "if", "theirs", "my", "against", "a", "by", "doing", "it", "how", "further", "was", "here", "than", "(", ")", "-", "/", ";"])

In [17]:
stop_pipeline = Pipeline(
    stages = [
      stop_words_cleaner
  ])

In [18]:
model = stop_pipeline.fit(annotations_df)
cleaned_df = model.transform(annotations_df)

In [19]:
display(cleaned_df)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos cleanTokens 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) List(List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 34, 41, location, Map(sentence -> 0), List()), List(token, 43, 44, is, Map(sentence -> 0), List()), List(token, 46, 52, central, Map(sentence -> 0), List()), List(token, 54, 55, to, Map(sentence -> 0), List()), List(token, 57, 60, lots, Map(sentence -> 0), List()), List(token, 62, 63, of, Map(sentence -> 0), List()), List(token, 65,

In [20]:
stop_words_cleaner = StopWordsCleaner() \
        .setInputCols(["token"]) \
        .setOutputCol("cleanTokens") \
        .setCaseSensitive(False) \
        .setStopWords(["this", "is", "and", ",", "!", ".", "\n", "\t", "ourselves", "hers", "between", "yourself", "but", "again", "there", "about", "once", "during", "out", "very", "having", "with", "they", "own", "an", "be", "some", "for", "do", "its", "yours", "such", "into", "of", "most", "itself", "other", "off", "is", "s", "am", "or", "who", "as", "from", "him", "each", "the", "themselves", "until", "below", "are", "we", "these", "your", "his", "through", "don", "nor", "me", "were", "her", "more", "himself", "this", "down", "should", "our", "their", "while", "above", "both", "up", "to", "ours", "had", "she", "all", "no", "when", "at", "any", "before", "them", "same", "and", "been", "have", "in", "will", "on", "does", "yourselves", "then", "that", "because", "what", "over", "why", "so", "can", "did", "not", "now", "under", "he", "you", "herself", "has", "just", "where", "too", "only", "myself", "which", "those", "i", "after", "few", "whom", "t", "being", "if", "theirs", "my", "against", "a", "by", "doing", "it", "how", "further", "was", "here", "than", "(", ")", "-", "/", ";"])

ngrams = NGramGenerator() \
            .setInputCols(["cleanTokens"]) \
            .setOutputCol("ngrams") \
            .setN(2) \
            .setEnableCumulative(False)

extra_pipeline = Pipeline(
    stages = [
      stop_words_cleaner,
      ngrams
  ])

In [21]:
model = extra_pipeline.fit(annotations_df)
new_df = model.transform(annotations_df)

In [22]:
display(new_df)

listing_id id date reviewer_id reviewer_name text document sentence token checked lemma stem pos cleanTokens ngrams 5456 16489 2009-11-07 46119 Kevin Very accommodating, great space. List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(document, 0, 31, Very accommodating, great space., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(sentence -> 0), List()), List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 18, 18, ,, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List()), List(token, 31, 31, ., Map(sentence -> 0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodating, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, Very, Map(confidence -> 1.0), List()), List(token, 5, 17, accommodate, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(token, 0, 3, veri, Map(confidence -> 1.0), List()), List(token, 5, 17, accommod, Map(confidence -> 1.0), List()), List(token, 18, 18, ,, Map(confidence -> 0.0), List()), List(token, 20, 24, great, Map(confidence -> 1.0), List()), List(token, 26, 30, space, Map(confidence -> 1.0), List()), List(token, 31, 31, ., Map(confidence -> 0.0), List())) List(List(pos, 0, 3, RB, Map(word -> Very), List()), List(pos, 5, 17, VBG, Map(word -> accommodating), List()), List(pos, 18, 18, ,, Map(word -> ,), List()), List(pos, 20, 24, JJ, Map(word -> great), List()), List(pos, 26, 30, NN, Map(word -> space), List()), List(pos, 31, 31, ., Map(word -> .), List())) List(List(token, 5, 17, accommodating, Map(sentence -> 0), List()), List(token, 20, 24, great, Map(sentence -> 0), List()), List(token, 26, 30, space, Map(sentence -> 0), List())) List(List(chunk, 5, 24, accommodating great, Map(sentence -> 0), List()), List(chunk, 20, 30, great space, Map(sentence -> 0), List())) 5456 18215 2009-11-24 54243 Jane 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen. List(List(document, 0, 217, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries. Place is clean, private and offers an array of videos and dcs. Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 0), List())) List(List(document, 0, 97, 6th Street is a bit of a walk but location is central to lots of shopping, nightlife and eateries., Map(sentence -> 0), List()), List(document, 99, 160, Place is clean, private and offers an array of videos and dcs., Map(sentence -> 1), List()), List(document, 162, 217, Great coffee, coffee pot and Fiesta Ware in the kitchen., Map(sentence -> 2), List())) List(List(token, 0, 2, 6th, Map(sentence -> 0), List()), List(token, 4, 9, Street, Map(sentence -> 0), List()), List(token, 11, 12, is, Map(sentence -> 0), List()), List(token, 14, 14, a, Map(sentence -> 0), List()), List(token, 16, 18, bit, Map(sentence -> 0), List()), List(token, 20, 21, of, Map(sentence -> 0), List()), List(token, 23, 23, a, Map(sentence -> 0), List()), List(token, 25, 28, walk, Map(sentence -> 0), List()), List(token, 30, 32, but, Map(sentence -> 0), List()), List(token, 34, 41, location, Map(sentence -> 0), List()), List(token, 43, 44, is, Map(sentence -> 0), List()), List(token, 46, 52, central, Map(sentence -> 0), List()), List(token, 54, 55, to, Map(sente